In [ ]:
def Conv_Block(inputs, model_width, num_row, num_col, activation='relu',  padding='same',batch_norm=False, name=None):
    # 2D Convolutional Block
    x = Conv2D(model_width , (num_row,num_col), padding=padding)(inputs)
    if batch_norm:
        x = BatchNormalization(axis=-1)(x)

    if not activation is None:
        x = Activation(activation, name=name)(x)
    # x = tf.keras.layers.BatchNormalization()(x)
    # x = tf.keras.layers.Activation('relu')(x)

    return x


def trans_conv2D(inputs, model_width, activation=None, strides=(2, 2), batch_norm=False, name=None):
    # 2D Transposed Convolutional Block, used instead of UpSampling
    x = Conv2DTranspose(model_width , (2, 2), strides=strides, padding='same')(inputs)  # Stride = 2, Kernel Size = 2
    if batch_norm:
        x = BatchNormalization(axis=-1)(x)
    x = BatchNormalization()(x)
    if not activation is None:
        x = Activation(activation, name=name)(x)
        # x = tf.keras.layers.Activation(activation,'relu')(x)

    return x


def Concat_Block(input1, *argv):
    # Concatenation Block from the Keras Library
    cat = input1
    for arg in range(0, len(argv)):
        cat = concatenate([cat, argv[arg]], axis=-1)

    return cat


def upConv_Block(inputs, size=(2, 2)):
    # 2D UpSampling Block
    up = UpSampling2D(size=size)(inputs)

    return up

def Attention_Block(skip_connection, gating_signal, num_filters):
    # Attention Block
    conv1x1_1 = Conv2D(num_filters, (1, 1), strides=(2, 2))(skip_connection)
    conv1x1_1 =BatchNormalization()(conv1x1_1)
    conv1x1_2 = Conv2D(num_filters, (1, 1), strides=(1, 1))(gating_signal)
    conv1x1_2 = BatchNormalization()(conv1x1_2)
    conv1_2 = add([conv1x1_1, conv1x1_2])
    conv1_2 = Activation('relu')(conv1_2)
    conv1_2 = Conv2D(1, (1, 1), strides=(1, 1))(conv1_2)
    conv1_2 = BatchNormalization()(conv1_2)
    conv1_2 = Activation('sigmoid')(conv1_2)
    resampler1 = upConv_Block(conv1_2)
    resampler2 = trans_conv2D(conv1_2, 1)
    resampler = add([resampler1, resampler2])
    out = skip_connection * resampler

    return out


def MultiResBlock(inputs, model_width, batch_norm=True, alpha=1.67, padding='same', activation='relu'):
    # MultiRes Block
    # U {int} -- Number of filters in a corrsponding UNet stage
    # inp {keras layer} -- input layer

    w = alpha * model_width

    shortcut = inputs
    shortcut = Conv_Block(shortcut, int(w * 0.167) + int(w * 0.333) + int(w * 0.5), 1, 1, activation=None,
                         batch_norm=batch_norm, padding='same')

    conv3x3 = Conv_Block(inputs, int(w * 0.167), 3, 3,activation=activation, padding=padding, batch_norm=batch_norm)
    conv5x5 = Conv_Block(conv3x3, int(w * 0.333), 3, 3,activation=activation, padding=padding, batch_norm=batch_norm)
    conv7x7 = Conv_Block(conv5x5, int(w * 0.5), 3, 3, activation=activation, padding=padding, batch_norm=batch_norm)

    out = concatenate([conv3x3, conv5x5, conv7x7], axis=-1)
    out = BatchNormalization()(out)
    out = Add()([shortcut, out])
    out = Activation(activation)(out)
    out = BatchNormalization()(out)

    return out


def ResPath(inputs, model_width, model_depth=5, batch_norm=True, padding='same'):
    # ResPath
    # filters {int} -- [description]
    # length {int} -- length of ResPath
    # inp {keras layer} -- input layer

    shortcut = inputs
    shortcut = Conv_Block(shortcut, model_width, 1, 1,activation=None, padding=padding, batch_norm=batch_norm)

    out = Conv_Block(inputs, model_width, 3, 3,  activation='relu', padding=padding, batch_norm=batch_norm)
    out = Add()([shortcut, out])
    out = Activation('relu')(out)
    out = BatchNormalization()(out)

    for _ in range(1, model_depth):
        shortcut = out
        shortcut = Conv_Block(shortcut, model_width, 1, 1,activation=None, padding=padding, batch_norm=batch_norm)

        out = Conv_Block(out, model_width, 3, 3,  activation='relu', padding=padding, batch_norm=batch_norm)
        out = Add()([shortcut, out])
        out = Activation('relu')(out)
        out = BatchNormalization()(out)

    return out

In [ ]:
class Bottleneck(layers.Layer):
    """
    注意：原论文中，在虚线残差结构的主分支上，第一个1x1卷积层的步距是2，第二个3x3卷积层步距是1。
    但在pytorch官方实现过程中是第一个1x1卷积层的步距是1，第二个3x3卷积层步距是2，
    这么做的好处是能够在top1上提升大概0.5%的准确率。
    可参考Resnet v1.5 https://ngc.nvidia.com/catalog/model-scripts/nvidia:resnet_50_v1_5_for_pytorch
    """
    expansion = 4

    def __init__(self, out_channel, strides=1, downsample=None, **kwargs):
        super(Bottleneck, self).__init__(**kwargs)
        self.conv1 = layers.Conv2D(out_channel, kernel_size=1, use_bias=False, name="conv1")
        self.bn1 = layers.BatchNormalization(momentum=0.9, epsilon=1e-5, name="conv1/BatchNorm")
        # -----------------------------------------
        self.conv2 = layers.Conv2D(out_channel, kernel_size=3, use_bias=False,
                                   strides=strides, padding="SAME", name="conv2")
        self.bn2 = layers.BatchNormalization(momentum=0.9, epsilon=1e-5, name="conv2/BatchNorm")
        # -----------------------------------------
        self.conv3 = layers.Conv2D(out_channel * self.expansion, kernel_size=1, use_bias=False, name="conv3")
        self.bn3 = layers.BatchNormalization(momentum=0.9, epsilon=1e-5, name="conv3/BatchNorm")
        # -----------------------------------------
        self.relu = layers.ReLU()
        self.downsample = downsample
        self.add = layers.Add()

    def call(self, inputs, training=False):
        identity = inputs
        if self.downsample is not None:
            identity = self.downsample(inputs)

        x = self.conv1(inputs)
        x = self.bn1(x, training=training)
        x = self.relu(x)

        x = self.conv2(x)
        x = self.bn2(x, training=training)
        x = self.relu(x)

        x = self.conv3(x)
        x = self.bn3(x, training=training)

        x = self.add([x, identity])
        x = self.relu(x)

        return x
def side_branch(x, factor):
#     x = Conv2D(1, (1, 1), activation=None, padding='same')(x)

    kernel_size = (2*factor, 2*factor)
    x = Conv2DTranspose(1, kernel_size, strides=factor, padding='same', use_bias=False, activation=None)(x)

    return x

def side_branch1(x):
    x = Conv2D(1, (1, 1), activation=None, padding='same')(x)

#     kernel_size = (2*factor, 2*factor)
#     x = Conv2DTranspose(1, kernel_size, strides=factor, padding='same', use_bias=False, activation=None)(x)
    x = MaxPooling2D((2, 2), strides=(2, 2), padding='same', name='block2_pool')(x)

    return x

def side_branch2(x):
    x = Conv2D(1, (1, 1), activation=None, padding='same')(x)

    return x

def maxpool(x, factor):   

#     kernel_size = (2*factor, 2*factor)
    x = MaxPooling2D((2, 2), strides = factor, padding='same')(x)
    x = Conv2D(1, (1, 1), activation=None, padding='same')(x)

    return x
class BasicBlock(layers.Layer):
    expansion = 1

    def __init__(self, out_channel, strides=1, downsample=None, **kwargs):
        super(BasicBlock, self).__init__(**kwargs)
        self.conv1 = layers.Conv2D(out_channel, kernel_size=3, strides=strides,
                                   padding="SAME", use_bias=False)
        self.bn1 = layers.BatchNormalization(momentum=0.9, epsilon=1e-5)
        # -----------------------------------------
        self.conv2 = layers.Conv2D(out_channel, kernel_size=3, strides=1,
                                   padding="SAME", use_bias=False)
        self.bn2 = layers.BatchNormalization(momentum=0.9, epsilon=1e-5)
        # -----------------------------------------
        self.downsample = downsample
        self.relu = layers.ReLU()
        self.add = layers.Add()

    def call(self, inputs, training=False):
        identity = inputs
        if self.downsample is not None:
            identity = self.downsample(inputs)

        x = self.conv1(inputs)
        x = self.bn1(x, training=training)
        x = self.relu(x)

        x = self.conv2(x)
        x = self.bn2(x, training=training)

        x = self.add([identity, x])
        x = self.relu(x)

        return x
def _make_layer(block, in_channel, channel, block_num, name, strides=1):
    downsample = None
    if strides != 1 or in_channel != channel * block.expansion:
        downsample = Sequential([
            layers.Conv2D(channel * block.expansion, kernel_size=1, strides=strides,
                          use_bias=False, name="conv1"),
            layers.BatchNormalization(momentum=0.9, epsilon=1.001e-5, name="BatchNorm")
        ], name="shortcut")

    layers_list = []
    layers_list.append(block(channel, downsample=downsample, strides=strides, name="unit_1"))

    for index in range(1, block_num):
        layers_list.append(block(channel, name="unit_" + str(index + 1)))

    return Sequential(layers_list, name=name)
def side_branch2(x):
    x = Conv2D(1, (1, 1), activation=None, padding='same')(x)

    return x
def bn_act(x, act=True):
    'batch normalization layer with an optinal activation layer'
    x = tf.keras.layers.BatchNormalization()(x)
    if act == True:
        x = tf.keras.layers.Activation('relu')(x)
    return x
def conv_block(x, filters, kernel_size=3, padding='same', strides=1):
    'convolutional layer which always uses the batch normalization layer'
    conv = bn_act(x)
    conv = Conv2D(filters, kernel_size, padding=padding, strides=strides)(conv)
    return conv
def stem(x, filters, kernel_size=3, padding='same', strides=1):
    conv = Conv2D(filters, kernel_size, padding=padding, strides=strides)(x)
    conv = conv_block(conv, filters, kernel_size, padding, strides)
    shortcut = Conv2D(filters, kernel_size=1, padding=padding, strides=strides)(x)
    shortcut = bn_act(shortcut, act=False)
    output = Add()([conv, shortcut])
    return output
def residual_block(x, filters, kernel_size=3, padding='same', strides=1):
    res = conv_block(x, filters, kernel_size, padding, strides)
    res = conv_block(res, filters, kernel_size, padding, 1)
    shortcut = Conv2D(filters, kernel_size, padding=padding, strides=strides)(x)
    shortcut = bn_act(shortcut, act=False)
    output = Add()([shortcut, res])
    return output
def upsample_concat_block(x, xskip):
    u = UpSampling2D((2,2))(x)
    c = Concatenate()([u, xskip])
    return c


#（1）深度可分离卷积+空洞卷积
def block(inputs, filters, rate):
    '''
    filters:1*1卷积下降的通道数
    rate:空洞卷积的膨胀率
    '''
 
    # 3*3深度卷积，指定膨胀率
    x = layers.DepthwiseConv2D(kernel_size=(3,3), strides=1, padding='same',
                               dilation_rate=rate, use_bias=False)(inputs)
 
    x = layers.BatchNormalization()(x)  # 标准化
    x = tf.keras.layers.PReLU()(x)  # 激活函数
 
    # 1*1逐点卷积调整通道数
    x = layers.Conv2D(filters, kernel_size=(1,1), strides=1, padding='same', use_bias=False)(x)
    
    x = layers.BatchNormalization()(x)  # 标准化
    x = tf.keras.layers.PReLU()(x)  # 激活函数
 
    return x
def aspp(inputs):
 
    # 获取输入图像的尺寸
    b,h,w,c = inputs.shape
 
    # 1*1标准卷积降低通道数[13,13,1024]==>[13,13,512]
    x1 = layers.Conv2D(filters=512, kernel_size=(1,1), strides=1, padding='same', use_bias=False)(inputs)
    x1 = layers.BatchNormalization()(x1)  # 标准化
    x1 = layers.Activation('relu')(x1)  # 激活
 
    # 膨胀率=1
    x2 = block(inputs, filters=512, rate=2)
    # 膨胀率=3
    x3 = block(inputs, filters=512, rate=6)
    # 膨胀率=5
    x4 = block(inputs, filters=512, rate=12)
 
    # 全局平均池化[13,13,1024]==>[None,1024]
    x5 = layers.GlobalAveragePooling2D()(inputs)
    # [None,1024]==>[1,1,1024]
    x5 = layers.Reshape(target_shape=[1,1,-1])(x5)
    # 1*1卷积减少通道数[1,1,1024]==>[1,1,512]
    x5 = layers.Conv2D(filters=512, kernel_size=(1,1), strides=1, padding='same', use_bias=False)(x5)
    x5 = layers.BatchNormalization()(x5)
    x5 = layers.Activation('relu')(x5)
    # 调整图像大小[1,1,512]==>[13,13,512]
    x5 = tf.image.resize(x5, size=(h,w))
    
    # 堆叠5个并行操作[13,13,512]==>[13,13,512*5]
    x = layers.concatenate([x1,x2,x3,x4,x5])
    x = eca_block(x)
    
    # 1*1卷积调整通道
    x = layers.Conv2D(filters=512, kernel_size=(1,1), strides=1, padding='same', use_bias=False)(x)
    x = layers.BatchNormalization()(x)
    x = tf.keras.layers.PReLU()(x)
    # 随机杀死神经元
    x = layers.Dropout(rate=0.1)(x)
 
    return x
def eca_block(inputs, b=1, gamma=2, name=""):
    channel = inputs.shape[-1]
    kernel_size = int(abs((math.log(channel, 2) + b) / gamma))
    kernel_size = kernel_size if kernel_size % 2 else kernel_size + 1
    avg_pool = GlobalAveragePooling2D()(inputs)
        
    x = Reshape((-1,1))(avg_pool)
    x = Conv1D(1, kernel_size=kernel_size, padding="same", use_bias=False,)(x)
    x = Activation('sigmoid')(x)
    x = Reshape((1, 1, -1))(x)

    output = multiply([inputs,x])
    return output

In [ ]:
def ResUNet_encoder(inp2):
    f = [16, 32, 64, 128, 256]

    e1 = stem(inp2, f[0])
    b1 = Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv1_')(inp2)
    b1 = Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv2_')(b1)
    b1 = eca_block(b1)
    e1 = Concatenate(axis=-1)([e1, b1])
    
    e2 = residual_block(e1, f[1], strides=2)
    b2 = Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv1_')(e2)
    b2 = Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv2_')(b2)
    b2 = eca_block(b2)
    e2 = Concatenate(axis=-1)([e2, b2])
  
    e3 = residual_block(e2, f[2], strides=2)
    b3 = Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv1_')(e3)
    b3 = Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv2_')(b3)
    b3 = Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv3_')(b3)
    b3 = eca_block(b3)
    e3 = Concatenate(axis=-1)([e3, b3])

    e4 = residual_block(e3, f[3], strides=2)
    b4 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv1_')(e4)
    b4 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv2_')(b4)
    b4 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv3_')(b4)
    b4 = eca_block(b4)
    e4 = Concatenate(axis=-1)([e4, b4])
    
    e5 = residual_block(e4, f[4], strides=2)
    b5 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv1_')(e5)
    b5 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv2_')(b5)
    b5 = Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv3_')(b5)
    b5 = eca_block(b5)
    e5 = Concatenate(axis=-1)([e5, b5])
    return b1,b2,b3,b4,b5

In [ ]:
import tensorflow as tf
from tensorflow.keras.layers import Input, Conv2D, Softmax
from tensorflow.keras.models import Model

def attention_mrunet(model_width, num_classes,model_depth=5):
    def f(x):
        b1, b2, b3, b4, b5 = ResUNet_encoder(x)
        mresblocks = {}
        levels = []

        D_S = 1
        A_G = 1
        LSTM = 0
        pool = x

        for i in range(1, (model_depth + 1)):
            mresblock = MultiResBlock(pool, model_width, 2 ** (i - 1))
            pool = MaxPooling2D(pool_size=(2, 2))(mresblock)
            mresblocks["mres%s" % i] = ResPath(mresblock, (model_depth - i + 1), model_width, 2 ** (i - 1))

        mresblock = MultiResBlock(pool, model_width, 2 ** model_depth)

        deconv = mresblock
        mresblocks_list = list(mresblocks.values())
        concat_blocks = [b5, b4, b3, b2, b1]

        for j in range(0, model_depth):
            skip_connection = mresblocks_list[model_depth - j - 1]
            concat_block = concat_blocks[j]
            if A_G == 1:
                skip_connection = Attention_Block(skip_connection, deconv, model_width)
            if D_S == 1:
                level = Conv2D(num_classes, (1, 1), name=f'level{model_depth - j}')(deconv)
                levels.append(level)
            deconv = upConv_Block(deconv)
            if LSTM == 0:
                deconv = Concat_Block(deconv, skip_connection)
                deconv = Concat_Block(deconv, concat_block)
            deconv = MultiResBlock(deconv, model_width, 2 ** (model_depth - j - 1))
        return deconv
    return f

def merge_model():
    inp = Input(shape=(256, 256, 3))

    num_classes = 16
    num_classes1 = 6

    # Get features from attention_mrunet
    features = attention_mrunet(model_width=64, num_classes=num_classes,model_depth=5)(inp)
  
    out6 = Conv2D(num_classes, kernel_size=1, activation='relu')(features)  # Processing 16 main classes
    out2 = Conv2D(num_classes1, kernel_size=1, activation='relu')(features)  # Processing 6 secondary classes
    
    # Add Softmax layers
    out16 = Softmax(axis=-1, name='out_16')(out6)
    out6 = Softmax(axis=-1, name='out_6')(out2)
    
    model = Model(inputs=inp, outputs=[out16, out6], name='merge_model')
    
    return model

if __name__ == '__main__':
    model = merge_model()
    model.summary()


In [8]:
pretrained_net=merge_model()
net = pretrained_net
net.summary()
plot_model(net, to_file='resnet_hed_all_1.png', show_shapes=True)


Model: "merge_model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 256, 256, 3) 0                                            
__________________________________________________________________________________________________
conv2d_732 (Conv2D)             (None, 256, 256, 17) 476         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1075 (Batch (None, 256, 256, 17) 68          conv2d_732[0][0]                 
__________________________________________________________________________________________________
activation_722 (Activation)     (None, 256, 256, 17) 0           batch_normalization_1075[0][0]   
________________________________________________________________________________________

activation_1161 (Activation)    (None, 32, 32, 2)    0           add_566[0][0]                    
__________________________________________________________________________________________________
conv2d_1029 (Conv2D)            (None, 64, 64, 3)    12          batch_normalization_1520[0][0]   
__________________________________________________________________________________________________
batch_normalization_1522 (Batch (None, 64, 64, 3)    12          conv2d_1030[0][0]                
__________________________________________________________________________________________________
activation_879 (Activation)     (None, 128, 128, 4)  0           add_427[0][0]                    
__________________________________________________________________________________________________
conv2d_747 (Conv2D)             (None, 256, 256, 5)  30          batch_normalization_1097[0][0]   
__________________________________________________________________________________________________
batch_norm

add_585 (Add)                   (None, 32, 32, 2)    0           batch_normalization_1788[0][0]   
                                                                 activation_1198[0][0]            
__________________________________________________________________________________________________
conv2d_1068 (Conv2D)            (None, 64, 64, 3)    84          batch_normalization_1577[0][0]   
__________________________________________________________________________________________________
add_446 (Add)                   (None, 128, 128, 4)  0           batch_normalization_1365[0][0]   
                                                                 activation_916[0][0]             
__________________________________________________________________________________________________
conv2d_786 (Conv2D)             (None, 256, 256, 5)  230         batch_normalization_1154[0][0]   
__________________________________________________________________________________________________
conv2d_134

conv2d_1395 (Conv2D)            (None, 8, 8, 64)     128         batch_normalization_2063[0][0]   
__________________________________________________________________________________________________
conv2d_1396 (Conv2D)            (None, 8, 8, 64)     6784        batch_normalization_2069[0][0]   
__________________________________________________________________________________________________
conv2d_730 (Conv2D)             (None, 16, 16, 256)  1474816     concatenate_29[0][0]             
__________________________________________________________________________________________________
activation_720 (Activation)     (None, 16, 16, 256)  0           batch_normalization_1072[0][0]   
__________________________________________________________________________________________________
add_606 (Add)                   (None, 32, 32, 2)    0           batch_normalization_1851[0][0]   
                                                                 activation_1240[0][0]            
__________

Total params: 18,497,101
Trainable params: 18,476,417
Non-trainable params: 20,684
__________________________________________________________________________________________________
